In [1]:
import drjit as dr
import mitsuba as mi
import numpy as np

mi.set_variant('cuda_ad_rgb')


[mitsuba] Warning: Couldn't import the ipywidgets package. Installing this package is required for the system to properly log messages and print in Jupyter notebooks!


In [2]:
scene = mi.load_file(r'C:\Users\HTCV_DIRME\Desktop\Projectwork\Blender_xml\Swimming_monke.xml')

print('I am here')

image = mi.render(scene, spp =512)


I am here


In [3]:
mi.util.convert_to_bitmap(image)


Bitmap[
  pixel_format = rgb,
  component_format = uint8,
  size = [1920, 1080],
  srgb_gamma = 1,
  struct = Struct<3>[
    uint8 R; // @0, normalized, gamma, premultiplied alpha
    uint8 G; // @1, normalized, gamma, premultiplied alpha
    uint8 B; // @2, normalized, gamma, premultiplied alpha
  ],
  data = [ 5.93 MiB of image data ]
]

In [4]:
params = mi.traverse(scene)
print(params)
key = 'elm__8.bsdf.brdf_0.base_color.value'
params_ref = mi.Color3f(params[key])
print(params_ref) 
params[key] = mi.Color3f(0.9,0.3,0.5)
params.update()


SceneParameters[
  -----------------------------------------------------------------------------------------------------------
  Name                                                    Flags    Type           Parent
  -----------------------------------------------------------------------------------------------------------
  elm__1.sampling_weight                                           float          PointLight
  elm__1.position                                                  Point3f        PointLight
  elm__1.intensity.value                                  ∂        Color3f        SRGBReflectanceSpectrum
  elm__2.near_clip                                                 float          PerspectiveCamera
  elm__2.far_clip                                                  float          PerspectiveCamera
  elm__2.shutter_open                                              float          PerspectiveCamera
  elm__2.shutter_open_time                                         float          

[(SRGBReflectanceSpectrum[
    value = [[0.9, 0.3, 0.5]]
  ],
  {'value'}),
 (Principled BSDF :
  base_color: SRGBReflectanceSpectrum[
    value = [[0.9, 0.3, 0.5]]
  ],
  spec_trans: UniformSpectrum[value=[0]],
  anisotropic: UniformSpectrum[value=[0]],
  roughness: UniformSpectrum[value=[0.25]],
  sheen: UniformSpectrum[value=[0]],
  sheen_tint: SRGBReflectanceSpectrum[
    value = [[1, 1, 1]]
  ],
  flatness: UniformSpectrum[value=[0]],
  specular: [0.5],
  clearcoat: UniformSpectrum[value=[0]],
  clearcoat_gloss: UniformSpectrum[value=[0.0009]],
  metallic: UniformSpectrum[value=[1]],
  spec_tint: SRGBReflectanceSpectrum[
    value = [[1, 1, 1]]
  ],,
  {'base_color'}),
 (TwoSided[
    brdf[0] = Principled BSDF :
    base_color: SRGBReflectanceSpectrum[
      value = [[0.9, 0.3, 0.5]]
    ],
    spec_trans: UniformSpectrum[value=[0]],
    anisotropic: UniformSpectrum[value=[0]],
    roughness: UniformSpectrum[value=[0.25]],
    sheen: UniformSpectrum[value=[0]],
    sheen_tint: SRG

In [5]:
rendered_img = mi.render(scene,spp=128)
mi.util.convert_to_bitmap(rendered_img)


Bitmap[
  pixel_format = rgb,
  component_format = uint8,
  size = [1920, 1080],
  srgb_gamma = 1,
  struct = Struct<3>[
    uint8 R; // @0, normalized, gamma, premultiplied alpha
    uint8 G; // @1, normalized, gamma, premultiplied alpha
    uint8 B; // @2, normalized, gamma, premultiplied alpha
  ],
  data = [ 5.93 MiB of image data ]
]

In [10]:
opt = mi.ad.Adam(lr=0.01)
opt[key] = params[key]
params.update(opt)

[(SRGBReflectanceSpectrum[
    value = [[0.226894, 0.831331, 0.382939]]
  ],
  {'value'}),
 (Principled BSDF :
  base_color: SRGBReflectanceSpectrum[
    value = [[0.226894, 0.831331, 0.382939]]
  ],
  spec_trans: UniformSpectrum[value=[0]],
  anisotropic: UniformSpectrum[value=[0]],
  roughness: UniformSpectrum[value=[0.25]],
  sheen: UniformSpectrum[value=[0]],
  sheen_tint: SRGBReflectanceSpectrum[
    value = [[1, 1, 1]]
  ],
  flatness: UniformSpectrum[value=[0]],
  specular: [0.5],
  clearcoat: UniformSpectrum[value=[0]],
  clearcoat_gloss: UniformSpectrum[value=[0.0009]],
  metallic: UniformSpectrum[value=[1]],
  spec_tint: SRGBReflectanceSpectrum[
    value = [[1, 1, 1]]
  ],,
  {'base_color'}),
 (TwoSided[
    brdf[0] = Principled BSDF :
    base_color: SRGBReflectanceSpectrum[
      value = [[0.226894, 0.831331, 0.382939]]
    ],
    spec_trans: UniformSpectrum[value=[0]],
    anisotropic: UniformSpectrum[value=[0]],
    roughness: UniformSpectrum[value=[0.25]],
    sheen: Un

In [11]:
def mse(image1):
    return dr.mean(dr.sqr(image1-image))

iteration_count = 50
print("full")

full


In [12]:
errors = []
for it in range(iteration_count):
    image1 = mi.render(scene, params, spp=4)
    loss = mse(image1)
    dr.backward(loss)
    opt.step()
    opt[key] = dr.clamp(opt[key], 0.0, 1.0)
    params.update(opt)
    err_ref = dr.sum(dr.sqr(params_ref - params[key]))
    print(f"Iteration{it:02d}: parameter error = {err_ref[0]:6f}", end='\r')
    errors.append(err_ref)
    print("\n Optimization complete.")

Iteration00: parameter error = 0.000695
 Optimization complete.
Iteration01: parameter error = 0.000173
 Optimization complete.
Iteration02: parameter error = 0.000003
 Optimization complete.
Iteration03: parameter error = 0.000065
 Optimization complete.
Iteration04: parameter error = 0.000189
 Optimization complete.
Iteration05: parameter error = 0.000241
 Optimization complete.
Iteration06: parameter error = 0.000201
 Optimization complete.
Iteration07: parameter error = 0.000124
 Optimization complete.
Iteration08: parameter error = 0.000072
 Optimization complete.
Iteration09: parameter error = 0.000072
 Optimization complete.
Iteration10: parameter error = 0.000117
 Optimization complete.
Iteration11: parameter error = 0.000181
 Optimization complete.
Iteration12: parameter error = 0.000243
 Optimization complete.
Iteration13: parameter error = 0.000284
 Optimization complete.
Iteration14: parameter error = 0.000291
 Optimization complete.
Iteration15: parameter error = 0.000259


In [13]:
image_final =mi.render(scene, spp=128)
mi.util.convert_to_bitmap(image_final)

Bitmap[
  pixel_format = rgb,
  component_format = uint8,
  size = [1920, 1080],
  srgb_gamma = 1,
  struct = Struct<3>[
    uint8 R; // @0, normalized, gamma, premultiplied alpha
    uint8 G; // @1, normalized, gamma, premultiplied alpha
    uint8 B; // @2, normalized, gamma, premultiplied alpha
  ],
  data = [ 5.93 MiB of image data ]
]